# Attack baseline sentiment analysis model

## install libraries



In [ ]:
!pip uninstall -y transformers transformer-smaller-training-vocab
!pip install transformers==4.30.0 transformer-smaller-training-vocab==0.2.3
!pip install textattack==0.3.10 torch>=2.0.0 scikit-learn>=1.0.0 joblib>=1.2.0 tqdm>=4.60.0 matplotlib>=3.7.0 seaborn>=0.12.0 openpyxl

Found existing installation: transformers 4.30.0
Uninstalling transformers-4.30.0:
  Successfully uninstalled transformers-4.30.0
Found existing installation: transformer-smaller-training-vocab 0.2.3
Uninstalling transformer-smaller-training-vocab-0.2.3:
  Successfully uninstalled transformer-smaller-training-vocab-0.2.3
  Using cached transformers-4.30.0-py3-none-any.whl.metadata (113 kB)
  Using cached transformer_smaller_training_vocab-0.2.3-py3-none-any.whl.metadata (7.9 kB)
Using cached transformers-4.30.0-py3-none-any.whl (7.2 MB)
Using cached transformer_smaller_training_vocab-0.2.3-py3-none-any.whl (12 kB)
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
sentence-transformers 4.1.0 requires transformers<5.0.0,>=4.41.0, but you have transformers 4.30.0 which is incompatible.


## Mount drive and load Model and data

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
import sys
import os
import numpy as np
import pandas as pd
import joblib
import logging
import warnings
warnings.filterwarnings('ignore')

from textattack.models.wrappers import ModelWrapper
from textattack.datasets import Dataset
from textattack.attack_recipes import TextFoolerJin2019, PWWSRen2019, DeepWordBugGao2018
from textattack.attacker import Attacker
from textattack.attack_args import AttackArgs
from sklearn.pipeline import Pipeline
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.linear_model import LogisticRegression
import matplotlib.pyplot as plt
import seaborn as sns

# Setup logging
logging.basicConfig(level=logging.INFO)
logger = logging.getLogger(__name__)

In [ ]:
# Define paths
DATA_DIR = "/content/drive/MyDrive/Colab Notebooks/Data_RO"
MODELS_DIR = f"{DATA_DIR}/models"
RESULTS_DIR = f"{DATA_DIR}/results"
ATTACKS_DIR = f"{RESULTS_DIR}/attacks/baseline"
os.makedirs(ATTACKS_DIR, exist_ok=True)

In [ ]:
# Load test data
data_path = f"{DATA_DIR}/processed_splits.pkl"
if not os.path.exists(data_path):
    raise FileNotFoundError(f"Processed data not found at {data_path}")

data = joblib.load(data_path)
X_test = data['X_test'][:3000]
y_test = data['y_test'][:3000]

# Convert to list of tuples with string labels
dataset = [(text, "negative" if label == 0 else "positive") for text, label in zip(X_test, y_test)]

# Create TextAttack Dataset
textattack_dataset = Dataset(
    dataset,
    label_names=["negative", "positive"],
    label_map={"negative": 0, "positive": 1}
)

In [ ]:
# Load or retrain baseline model
model_path = f"{MODELS_DIR}/baseline_model.pkl"

def check_fitted_pipeline(pipeline):
    """Check if the pipeline's TF-IDF vectorizer is fitted."""
    try:
        # Check if the TfidfVectorizer is fitted by accessing its vocabulary
        tfidf = pipeline.named_steps['tfidf']
        if tfidf.vocabulary_ is None:
            return False
        return True
    except AttributeError:
        return False

def train_pipeline(X_train, y_train):
    """Train a new pipeline if the saved one is not fitted."""
    logger.info("Training a new pipeline...")
    pipeline = Pipeline([
        ('tfidf', TfidfVectorizer(max_features=5000)),
        ('clf', LogisticRegression(max_iter=1000))
    ])
    pipeline.fit(X_train, y_train)
    logger.info("Pipeline trained successfully.")
    # Save the newly trained pipeline
    joblib.dump(pipeline, model_path)
    logger.info(f"Saved newly trained pipeline to {model_path}")
    return pipeline

In [ ]:
# Load baseline model
if not os.path.exists(model_path):
    logger.warning(f"Baseline model not found at {model_path}. Training a new model...")
    if 'X_train' not in data or 'y_train' not in data:
        raise FileNotFoundError("Training data (X_train, y_train) not found in processed_splits.pkl")
    pipeline = train_pipeline(data['X_train'], data['y_train'])
else:
    try:
        pipeline = joblib.load(model_path)
        if not isinstance(pipeline, Pipeline):
            raise ValueError("Loaded object is not a sklearn Pipeline")
        if not check_fitted_pipeline(pipeline):
            logger.warning("Loaded pipeline is not fitted. Retraining...")
            if 'X_train' not in data or 'y_train' not in data:
                raise FileNotFoundError("Training data (X_train, y_train) not found in processed_splits.pkl")
            pipeline = train_pipeline(data['X_train'], data['y_train'])
        else:
            logger.info("Loaded fitted pipeline successfully")
    except Exception as e:
        logger.error(f"Failed to load baseline model: {str(e)}")
        raise

In [ ]:
class CustomModelWrapper(ModelWrapper):
    def __init__(self, pipeline):
        self.model = pipeline

    def __call__(self, text_input_list):
        return self.model.predict_proba(text_input_list)

wrapped_model = CustomModelWrapper(pipeline)

In [ ]:
def run_attack(attack_class, attack_name):
    output_dir = f"{ATTACKS_DIR}/{attack_name}"
    os.makedirs(output_dir, exist_ok=True)

    attack_args = AttackArgs(
        num_examples=3000,
        log_to_csv=f"{output_dir}/{attack_name}_attacked.csv",
        log_to_txt=f"{output_dir}/attack_summary.txt"
    )

    attacker = Attacker(attack_class.build(wrapped_model), textattack_dataset, attack_args)
    results = attacker.attack_dataset()

    # Save results
    result_df = pd.DataFrame({
        'original_text': [r.original_text() for r in results],
        'perturbed_text': [r.perturbed_text() if r.perturbed_text else "" for r in results],
        'ground_truth': [getattr(r, 'ground_truth_output', None) for r in results],  # Safely access ground_truth_output
        'result_type': [str(r) for r in results]
    })

    result_df.to_csv(f"{output_dir}/{attack_name}_attacked.csv", index=False)
    result_df.to_excel(f"{output_dir}/{attack_name}_attacked.xlsx", index=False)
    logger.info(f"Saved {attack_name} results to {output_dir}")
    return result_df

In [ ]:
import nltk
nltk.download('averaged_perceptron_tagger_eng')

[nltk_data] Downloading package averaged_perceptron_tagger_eng to
[nltk_data]     /root/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger_eng is already up-to-
[nltk_data]       date!


True

In [ ]:
attacks = {
    "TextFooler": TextFoolerJin2019,
    "PWWS": PWWSRen2019,
    "DeepWordBug": DeepWordBugGao2018
}

for name, attack_class in attacks.items():
    logger.info(f"\nRunning {name} attack...\n")
    output_dir = f"{ATTACKS_DIR}/{name}"
    df = run_attack(attack_class, name)

    # Plot success types
    success_rates = df['result_type'].value_counts()
    plt.figure(figsize=(10, 6))
    sns.barplot(x=success_rates.values, y=success_rates.index, palette="viridis")
    plt.title(f"{name} - Attack Result Types")
    plt.xlabel("Count")
    plt.ylabel("Result Type")
    plt.tight_layout()
    plt.savefig(f"{output_dir}/{name}_results.png")
    plt.close()
    logger.info(f"Saved plot for {name} at {output_dir}/{name}_results.png")

textattack: Unknown if model of class <class 'sklearn.pipeline.Pipeline'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to text file at path /content/drive/MyDrive/Colab Notebooks/Data_RO/results/attacks/baseline/TextFooler/attack_summary.txt
textattack: Logging to CSV at path /content/drive/MyDrive/Colab Notebooks/Data_RO/results/attacks/baseline/TextFooler/TextFooler_attacked.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.840845057
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
       

  0%|          | 0/3000 [11:46<?, ?it/s]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 2 / 3:   0%|          | 3/3000 [00:16<4:32:32,  5.46s/it]

--------------------------------------------- Result 1 ---------------------------------------------
[[Negative (95%)]] --> [[Positive (72%)]]

isplayer [[died]] [[sorry]]

isplayer [[chip]] [[excuse]]


--------------------------------------------- Result 2 ---------------------------------------------
[[Positive (67%)]] --> [[[SKIPPED]]]

wait release guessing photo placed myspace watch die


--------------------------------------------- Result 3 ---------------------------------------------
[[Positive (76%)]] --> [[[SKIPPED]]]

natasha may able see weekend next free certain get excited hope




[Succeeded / Failed / Skipped / Total] 2 / 0 / 2 / 4:   0%|          | 4/3000 [00:16<3:28:36,  4.18s/it]

...

--------------------------------------------- Result 2995 ---------------------------------------------
[[Negative (60%)]] --> [[Positive (53%)]]

looking creative us [[split]] toning color calibration option lightroom could find book bought

looking creative us [[pslit]] toning color calibration option lightroom could find book bought


--------------------------------------------- Result 2996 ---------------------------------------------
[[Positive (64%)]] --> [[Negative (55%)]]

back [[interesting]] email

back [[intQresting]] email




[Succeeded / Failed / Skipped / Total] 1932 / 316 / 750 / 2998: 100%|█████████▉| 2998/3000 [04:16<00:00, 11.70it/s]

--------------------------------------------- Result 2997 ---------------------------------------------
[[Negative (80%)]] --> [[Positive (54%)]]

[[sorry]] [[could]] talkative guy last nite get mad quotsocialquot lol

[[soriry]] [[couLld]] talkative guy last nite get mad quotsocialquot lol


--------------------------------------------- Result 2998 ---------------------------------------------
[[Negative (94%)]] --> [[Positive (56%)]]

farewell belinda [[even]] [[though]] [[really]] twitter technically saying one [[sad]]

farewell belinda [[eevn]] [[htough]] [[reagly]] twitter technically saying one [[lad]]




[Succeeded / Failed / Skipped / Total] 1934 / 316 / 750 / 3000: 100%|██████████| 3000/3000 [04:16<00:00, 11.70it/s]


--------------------------------------------- Result 2999 ---------------------------------------------
[[Negative (53%)]] --> [[Positive (57%)]]

[[ahhh]] sunday night

[[ahhY]] sunday night


--------------------------------------------- Result 3000 ---------------------------------------------
[[Positive (68%)]] --> [[Negative (60%)]]

[[talking]] cass emma [[hey]] guy

[[taking]] cass emma [[ehy]] guy



+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 1934   |
| Number of failed attacks:     | 316    |
| Number of skipped attacks:    | 750    |
| Original accuracy:            | 75.0%  |
| Accuracy under attack:        | 10.53% |
| Attack success rate:          | 85.96% |
| Average perturbed word %:     | 36.85% |
| Average num. words per input: | 6.88   |
| Avg num queries:              | 18.09  |
+-------------------------------+--------+
